# Data Warehouse Hack Part 1

What would you do if you were given access to a data set and did not have a data model?

What could you learn?  What sense could you make of the data?

### First things first

What are the tables and columns? Can you make any sense of them.

First we probably need to add the Oracle driver to our Python distribution:

```
pip3 install cx_Oracle
```

You may also need the Oracle instant client libraries.  Follow the instructions here: https://www.oracle.com/technetwork/database/database-technologies/instant-client/overview/index.html

In [1]:
import cx_Oracle
import networkx as nx
import json
import matplotlib.pyplot as plt
import numpy as np
import mpld3
import pickle
%matplotlib inline

## Dump a list of the DW Tablem Names

The following dumps all the tables that belong to DW (Data Warehouse).
JGI's Oracle instance has several thousand tables that are spread across a number of schemas.
In MySQL, PostGres, and other RDBMS (Relational Database Management Systems), these are called databases.
In Oracle schema and owner is synonymous.

We can get the list of tables by querying Oracle with

```
select table_name, num_rows from all_tables where owner = 'DW';
```

If we did not add the where clause (where owner = 'DW') we would see all the thousands of tables.

In [ ]:
con = cx_Oracle.connect('dw_user', 'dw_user', 'gpodb09.jgi-psf.org/dwdev1')
# print(con.version)
cur1 = con.cursor()

cur1.execute("select table_name, num_rows from all_tables where owner = 'DW'")
for result in sorted(cur1):
    table, rows = result
    print("Table %-30.30s Rows: %s" % (table, rows))
cur1.close()
con.close()

## Reviewing the table list

What do you notice about these tables?

- Are there empty tables?
- What purpose do the small tables serve?
- Can you guess what CV stands for?
- Do any tables look like they may be temporary or throw-away tables?

Well first notice the CV and the small tables mostly seem to be one in the same.  JGI tends to use name tables with a \_CV at
the end when these tables hold Control (or Controlled) Vocabulary.  Think of these tables as contains a defined list of values
for a drop-down box or some other usage that JGI wants to limit to predefined values (for example product types, sequencing platforms, etc).

## Next we'll look at the fields and see if there is anything we can discover

In [ ]:
con = cx_Oracle.connect('dw_user', 'dw_user', 'gpodb09.jgi-psf.org/dwdev1')
# print(con.version)

cur1 = con.cursor()
cur2 = con.cursor()

schema = {}

cur1.execute("select table_name, num_rows from all_tables where owner = 'DW'")
for result in sorted(cur1):
    table, rows = result
    print("Table %-30.30s Rows: %s" % (table, rows))
    # Save off our table data
    schema[table] = {'rows':rows, 'columns': []}

    cur2.execute("select column_name, data_type from all_tab_columns where table_name='%s' and owner='DW'" % table)
    for result in cur2:
        col, col_type = result
        print("      %s %s" % (col, col_type))
        # Save off the colums
        schema[table]['columns'].append((col, col_type))
    print()

cur1.close()
cur2.close()
con.close()

# Reviewing the column names

The first thing to look for are key values that link tables together.  These can be any data type, but an industry standard is to make these
integers (or perhaps a fixed length character string).

One thing you might notice is that every table has fields that end in an \_ID.   As it turns out, the Data Warehouse team has consistently named key fields with an \_ID at the end.  In other organizations you might see a PK (for Primary Key) or FK (for Foreign Key) added the field name.
This convention helps the reader know if the key is a primary key (i.e., the main and/or unique key value in the table), or is used to link link a table to an other table that holds the primary values.

For example a product table would have a unique primary key for every product in the catalog.  For a sales table, you would have many entries with the same (foreign) key pointing back to the (primary) key in the table that 'owns' the data.

### Saving off the data so far...

One thing we can do in Python and Jupyter is to save off the data we've collected.  This way we can save our Jupyter notebook and come back
later to examine the data without having to reattach to the database (for example if you wanted to work from home and did not want to get
on the VPN to connect to the database).

In [ ]:
# Save our object to disk
with open("schema.pickle", "wb") as f:
    pickle.dump(schema, f)

### Loading the data

For completeness, this is how you would load previously saved data set

In [ ]:
# Load our file from disk
# Needed only if we are want to load a saved copy
# (i.e. you don't want to reload from Oracle or you are not on the lbl network)
with open("schema.pickle", "rb") as f:
    schema = pickle.load(f)

## Visualing the data

Lets visualize the data we have so far.   First we'll produce a list of \*\_ID fields and what tables they are in.  This will help us
graph the data.

In [ ]:
def generate_edges(data, drop=[]):    
    # Generate a list of our edges
    edges = {}  # Edges will be used to store a list of *_ID fields and the tables where these are used
    for table in data:
        # Save off the table if we have data in the table and the name doens't contain any of these substrings
        if data[table]['rows'] and not any(substring in table for substring in drop):
            for column, column_type in data[table]['columns']:
                # Create a link if it is a *_ID field
                if '_ID' in column:
                    edges.setdefault(column, []).append(table)
    return edges
edges = generate_edges(schema)
for edge in edges:
    print(edge, ":", edges[edge])

## Drawing the Graph

Next, we'll borrow some code from the last data hand and graph these.

In [ ]:
# Create a graph of our data
# We'll add a drop feature so we can trim tables out of our graph at some point
def graph_dw(data, title=None, drop=[]):    
    # Generate a list of our edges
    edges = generate_edges(data, drop)

    # Create a directed graph
    G = nx.Graph()
    plt.figure(figsize=(40, 40))
    node_size = 4000

    # Save off the names of tables that we have edges for
    nodes = {}
    links = []  # Links will contain the list of links (will also be written to graph.json for later plotting)
    
    # Add in our edges, this will drop any table that doesn't link to any other table
    for col in edges:
        if len(edges[col]) > 1:
            # Save off the tables
            for table in edges[col]:
                nodes[table] = 1
            for i in range(0, len(edges[col]) - 1):
                for j in range(i+1, len(edges[col])):
                    G.add_edge(edges[col][i].replace('_', '\n'), edges[col][j].replace('_', '\n'))
                    links.append({'source': edges[col][i], 'target': edges[col][j], 'column': col})

    # Get the position of our nodes based on kamada kawai
    pos = nx.kamada_kawai_layout(G)

    # Draw the nodes, labels, and edges
    nx.draw_networkx_nodes(G, pos, node_size=node_size, node_color='lightskyblue')
    nx.draw_networkx_labels(G, pos, font_size=12)
    nx.draw_networkx_edges(G, pos, node_size=node_size, width=1, edge_color='grey')

    ax = plt.gca()
    ax.set_axis_off()
    if title: plt.title(title + ' (with at least 1 link)', fontsize=20)
    plt.show()
    
    # Save our graph as a JSON document
    with open('graph.json', 'w') as f:
        json.dump({'nodes': [{"name": node} for node in nodes], 'links': links}, f, indent=4)

graph_dw(schema, title='Data Warehouse Tables')

## What have we learned from this?

First you'll notice there is a high degree of connectivity in this graph.  If we look at the code we'll notice that we've linked every key
together.  We have also linked together keys where there is no primary table.

To visualize, we've created a fully connected graph (graph on left below), verses a graph that just connects the primary key to foreign key (graph on right):

![Graph1](http://portal.nersc.gov/project/m342/datahack-dw/Graph1.jpg)

It is important to note that just because two tables share a key, joining these two tables together may valid.

Let's rewrite our edge generator to delete any keys where there is no primary key (i.e., there is no *entity* for a *entity*\_ID field.  We'll also consider plural
table names as there seems to be a few.

In [ ]:
def generate_edges(data, drop=[]):    
    # Generate a list of our edges
    edges = {}  # Edges will be used to store a list of *_ID fields and the tables where these are used
    for table in data:
        # Save off the table if we have data in the table and the name doens't contain any of these substrings
        if data[table]['rows'] and not any(substring in table for substring in drop):
            for column, column_type in data[table]['columns']:
                # Create a link if it is a *_ID field and doesn't have a BY in it (created_by_id, etc)
                if '_ID' in column and 'BY_' not in column:
                    edges.setdefault(column, []).append(table)
    # Remove any edges where the column name (- '_ID') is not a table name too (looking for base tables)
    for edge in list(edges.keys()):
        if edge.replace('_ID', '') not in edges[edge] and \
           edge.replace('_ID', 's') not in edges[edge]: 
            # We can also make sure we get the CV tables, but let us ignore them for now
            # edge.replace('_ID', '_CV') not in edges[edge]:
            del edges[edge]
    return edges
edges = generate_edges(schema)
for edge in edges:
    print(edge, ":", edges[edge])

# Redefine our graph code

We'll also redefine our graph code to only link between primary and foreign keys and not show any links between foreign keys.

In [ ]:
# Create a graph of our data
def graph_dw(data, title=None, drop=[]):    
    # Generate a list of our edges
    edges = generate_edges(data, drop)

    # Create a directed graph
    G = nx.Graph()
    plt.figure(figsize=(40, 40))
    node_size = 4000

    # Save off the names of tables that we have edges for
    nodes = {}
    links = []  # Links will contain the list of links (will also be written to graph.json for later plotting)
    
    # Add in our edges, this will drop any table that doesn't link to any other table
    for col in edges:
        if len(edges[col]) > 1:
            # Save off the tables
            for table in edges[col]:
                nodes[table] = 1
            base = col.replace('_ID', '')
            for i in range(0, len(edges[col])):
                if edges[col][i] != base:
                    G.add_edge(base.replace('_', '\n'), edges[col][i].replace('_', '\n'))
                    links.append({'source': base, 'target': edges[col][i], 'column': col})

    # Get the position of our nodes based on kamada kawai
    pos = nx.kamada_kawai_layout(G)

    # Draw the nodes, labels, and edges
    nx.draw_networkx_nodes(G, pos, node_size=node_size, node_color='lightskyblue')
    nx.draw_networkx_labels(G, pos, font_size=12)
    nx.draw_networkx_edges(G, pos, node_size=node_size, width=1, edge_color='grey')

    ax = plt.gca()
    ax.set_axis_off()
    if title: plt.title(title + ' (with at least 1 link)', fontsize=20)
    plt.show()
    
    # Save our graph as a JSON document
    with open('graph.json', 'w') as f:
        json.dump({'nodes': [{"name": node} for node in nodes], 'links': links}, f, indent=4)

graph_dw(schema, title='Data Warehouse Tables')

# Drop tables that appear to be auxiliary tables

You've might have noticed that we've added some code to have the ability to drop tables out if we wanted to.  Looking at the above graph, we can see there are History tables, temp tables, reports, and a number of other extra tables that we might not care out.   Lets enumerate those and drop them from the graph.


In [ ]:
graph_dw(schema, title='Data Warehouse Tables', drop=['TMP', 'TEMP', 'REPORT', 'HIST', 'STATS', 'VFRZ', 'M2M', 'USS_', 'SAM_', 'GOLD_', 'SOW_', '_STAT', 'CLARITY_', '_DET', 'CLEAN', 'VCNT', 'IDS', 'QUEUE'])

## Creating an interactive graph

There are several ways you can create an interactive graph in Jupyter (D3, Plotly, Anovio, etc).  Below is some code written in D3 (Data-Driven-Documents) that will produce a graph you can
click on and drag around nodes (or hover over to get information).
As an aside, most of the interactive graphics you find on the New York Times web-site, are written using D3.

Note you can click on a node to drag it to a new location.  Double click on a node to release it.

In [ ]:
%%html
<!DOCTYPE html>
<meta charset="utf-8">
<style>
    .link {
        stroke: #ddd;
        stroke-width: 2px;
        pointer-events: all;
    }

    .node circle {
        pointer-events: all;
        stroke: #fff;
        stroke-width: 1.5px;
    }

    div.tooltip {
        position: absolute;
        background-color: white;
        max-width: 400px;
        height: auto;
        padding: 1px;
        border-style: solid;
        border-radius: 4px;
        border-width: 1px;
        box-shadow: 3px 3px 10px rgba(0, 0, 0, .5);
        pointer-events: none;
    }
</style>
<body>
</body>
<svg width="1200" height="1200"></svg>
<script src="https://d3js.org/d3.v4.min.js"></script>
<script src="https://cdnjs.cloudflare.com/ajax/libs/d3-legend/2.24.0/d3-legend.min.js"></script>

In [ ]:
%%javascript
var tooltip = d3.select('body')
    .append('div')
    .attr('class', 'tooltip')
    .style('opacity', 0);

d3.json('/files/graph.json', function (error, graph) {
    if (error) throw error;
    const svg = d3.select('svg'),
        width = +svg.attr('width'),
        height = +svg.attr('height'),
        R = 10;

    const simulation = d3.forceSimulation()
        .nodes(graph.nodes)
        .force('link', d3.forceLink().id(d => d.name))
        .force('charge', d3.forceManyBody().strength(-100))
        .force('collision', d3.forceCollide().radius(function (d) {return R * 4}))
        .force('x', d3.forceX())
        .force('y', d3.forceY())
        .force('center', d3.forceCenter(width / 2, height / 2))
        .on('tick', ticked);

    simulation.force('link')
        .links(graph.links);

    let link = svg.selectAll('line')
        .data(graph.links)
        .enter().append('line');

    link
        .attr('class', 'link')
        .on('mouseover.tooltip', function (d) {
            tooltip.transition()
                .duration(300)
                .style('opacity', .8);
            tooltip.html('Source: ' + d.source.name +
                '<br>Targe: ' + d.target.name + 
                '<br>Column: ' + d.column)
                .style('left', (d3.event.pageX) + 'px')
                .style('top', (d3.event.pageY + 10) + 'px');
        })
        .on('mouseout.tooltip', function () {
            tooltip.transition()
                .duration(100)
                .style('opacity', 0);
        });

    let node = svg.selectAll('.node')
        .data(graph.nodes)
        .enter().append('g')
        .attr('class', 'node')
        .call(d3.drag()
            .on('start', dragstarted)
            .on('drag', dragged)
            .on('end', dragended));

    node.append('circle')
        .attr('r', R)
        .attr('fill', 'lightskyblue')
        .on('mouseover.fade', fade(0.1))
        .on('mouseover', function() {
            d3.select(this)
              .transition().duration(300)
              .style('fill', 'orange')
              .attr('r', R*1.5);
        })
        .on('mouseout.fade', fade(1))
        .on('mouseout', function() {
            d3.select(this)
              .transition().duration(300)
              .style('fill', 'lightskyblue')
              .attr('r', R);
        })
        .on('dblclick', releasenode);

    node.append('text')
        .attr('x', 0)
        .attr('dy', '.35em')
        .text(d => d.name);

    function ticked() {
        link
            .attr('x1', d => d.source.x)
            .attr('y1', d => d.source.y)
            .attr('x2', d => d.target.x)
            .attr('y2', d => d.target.y);
        node
            .attr('transform', d => `translate(${d.x},${d.y})`);
    }

    function dragstarted(d) {
        if (!d3.event.active) simulation.alphaTarget(0.3).restart();
        d.fx = d.x;
        d.fy = d.y;
    }

    function dragged(d) {
        d.fx = d3.event.x;
        d.fy = d3.event.y;
    }

    function dragended(d) {
        if (!d3.event.active) simulation.alphaTarget(0);
    }

    function releasenode(d) {
        d.fx = null;
        d.fy = null;
    }

    const linkedByIndex = {};
    graph.links.forEach(d => {
        linkedByIndex[`${d.source.index},${d.target.index}`] = 1;
    });

    function isConnected(a, b) {
        return linkedByIndex[`${a.index},${b.index}`] || linkedByIndex[`${b.index},${a.index}`] || a.index === b.index;
    }

    function fade(opacity) {
        return d => {
            node.style('stroke-opacity', function (o) {
                const thisOpacity = isConnected(d, o) ? 1 : opacity;
                this.setAttribute('fill-opacity', thisOpacity);
                return thisOpacity;
            });
            link.style('stroke-opacity', o => (o.source === d || o.target === d ? 1 : opacity));
        };
    }
});

## Join Path 

One thing about Relational databases, is that join path is not explicitly listed in the data model.
SQL does provide for a mechanism to include this in the model to help the RDBMS ( enforce referential integrity.
But for the casual user, this is not available for writing queries.  As mentioned above, database designers will rely on some standards to help users
figure out what links to what.

This brings up an important point that there might be multiple valid join paths through a database.  In SQL you just have to know what these mean (or reason out for yourself what it might mean).   So for example, the following graph connects the same nodes we saw above in two different ways.  You as the user need to know
if this is valid and what it means.

![Graph2](http://portal.nersc.gov/project/m342/datahack-dw/Graph2.jpg)

For a Graph Database, relationships (join paths) are part of the design.  While you may need to know what attributes to transit on, all relationships are valid.
So in the above case, you don't need to specify how to get from point A to point E, the database knows how to get there (if there is a path).